In [1]:
import tensorflow as tf
import tensorflow_quantum as tfq

2021-12-20 14:48:31.552650: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2021-12-20 14:48:31.552704: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
2021-12-20 14:48:43.293925: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2021-12-20 14:48:43.294001: W tensorflow/stream_executor/cuda/cuda_driver.cc:326] failed call to cuInit: UNKNOWN ERROR (303)
2021-12-20 14:48:43.294046: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (maris083.lorentz.leidenuniv.nl): /proc/driver/nvidia/version does not exist
2021-12-20 14:48:43.299861: I tensorflow/core/

In [2]:
'''
import tensorflow_quantum as tfq

import cirq
import sympy

import glob
import imageio
import matplotlib.pyplot as plt

import os
import PIL

import time
import pandas as pd
from scipy.special import lambertw
from scipy.stats import wasserstein_distance
from IPython import display
from tqdm.notebook import tqdm


'''
import data_handling as dh
import stylized as st
import tensorflow as tf
from tensorflow.keras import layers
import numpy as np
from functools import reduce
import models as md
from tqdm import tqdm
import ray
from ray.util import inspect_serializability
import os
from datetime import datetime as dt
import matplotlib.pyplot as plt
@ray.remote
class quantum_GAN(object):
    def __init__(self, chopsize, stride, n_qubits, n_layers, epochs, save = False, run_id = 1, path = './'):
        import cirq#weird ray stuff        
        lr = 5e-4
        self.chopsize = chopsize
        self.stride = stride
        self.n_qubits = n_qubits
        self.n_layers = n_layers
        self.epochs = epochs
        self.save = save
        self.run_id = run_id
        self.log_returns_sp500 = dh.load_SP500_lr()
        self.lr = lr
        self.generator_optimizer = tf.keras.optimizers.Adam(lr)
        self.discriminator_optimizer = tf.keras.optimizers.Adam(lr)
        self.qubits = cirq.GridQubit.rect(1, n_qubits)
        self.observables = self.generate_observables()
        self.transformed_lr, self.transform_params = dh.transform(self.log_returns_sp500)
        self.noise_dim = n_qubits
        self.train_time_series = dh.chopchop(self.transformed_lr, chopsize, stride)
        self.train_time_series = self.train_time_series.reshape(self.train_time_series.shape[0], self.train_time_series.shape[1]).astype('float32')
        self.BUFFER_SIZE = self.train_time_series.shape[0]
        self.BATCH_SIZE = self.train_time_series.shape[0] // 10
        self.generator = md.generate_model_policy(self.qubits, self.n_layers, self.chopsize, self.observables)
        self.discriminator = md.make_discriminator_model(self.chopsize, self.noise_dim)
        self.dimension_image_alpha = [1] * len(self.discriminator.input_shape[1:])
        self.gradient_penalty_weight = 10.0
        self.nb_steps_update_critic = 5
        self.loss_gen = []
        self.loss_disc, self.loss_disc, self.loss_wass, self.loss_ACF, self.loss_ACF_nonabs, self.loss_leverage, self.loss_epochs = [],[],[],[],[],[],[]
        self.benchmarks, self.benchmark_lags = None, None
        if save:
            self.path = path+'/{}'.format('run_'+str(run_id))
            self.weight_path = self.path+'/weights'
            self.plot_path = self.path+'/plots'
            self.metrics_path = self.path+'/metrics'
            os.mkdir(self.path)
            os.mkdir(self.weight_path)
            os.mkdir(self.plot_path)
            os.mkdir(self.metrics_path)
            
    def generate_observables(self):
        import cirq 
        ops1 = [cirq.Z(q) for q in self.qubits]
        observables1 = [reduce((lambda x, y: x * y), ops1)] # Z_0*Z_1*Z_2*Z_3
        ops2 = [cirq.X(q) for q in self.qubits]
        observables2 = [reduce((lambda x, y: x * y), ops2)] # Z_0*Z_1*Z_2*Z_3        
        observables = observables1 + observables2 
        return observables
    
    def wasserstein_loss_critic(self, real_output: tf.Tensor, fake_output: tf.Tensor) -> tf.Tensor:
        """The Wasserstein loss of the discriminator from its output on fake and real data.
    
        :param real_output: Output of the discriminator when given real data.
        :param fake_output: Output of the discriminator when given fake data from generator.
    
        :return: Wasserstein loss evaluation for the discriminator
    
        """
        real_loss = tf.reduce_mean(real_output)
        fake_loss = tf.reduce_mean(fake_output)
        return fake_loss - real_loss
    
    def wasserstein_loss_generator(self, fake_output: tf.Tensor) -> tf.Tensor:
        """The Wasserstein loss of the generator from the output of the discriminator on fake data.
    
        :param fake_output: Output of the discriminator when given fake data from generator.
    
        :return: Cross entropy with Fake/True labels given by discriminator.
    
        """
    
        return -tf.reduce_mean(fake_output)
    
    @tf.function
    def gradient_penalty(self, critic:tf.keras.Model, fake_generator_output: tf.Tensor, images: tf.Tensor) -> tf.Tensor:
        """ Penalty from the gradients"""
    
        alpha = tf.random.uniform(
            [images.shape[0]] + self.dimension_image_alpha, 0.0, 1.0
        )
        difference_fake_real = fake_generator_output - images
        interpolation = images + (alpha * difference_fake_real)
        with tf.GradientTape() as tape:
            tape.watch(interpolation)
            preds = critic(interpolation, training=True)
        gradients = tape.gradient(preds, [interpolation])[0]
        slopes = tf.sqrt(tf.reduce_sum(tf.square(gradients), axis=[1]))#, 2, 3
        gp = tf.reduce_mean((slopes - 1.0) ** 2)
        return gp
    
    @tf.function
    def train_generator(self, gan_instance:tf.keras.Model, critic:tf.keras.Model, noise: tf.Tensor):
        """ Update the generator parameter with its optimizer"""
    
        with tf.GradientTape() as tape:
            generated_images = gan_instance(noise, training=False)
            #generated_images = tf.expand_dims(generated_images, -1)
            fake_output = critic(generated_images, training=True)
    
            gen_loss = self.wasserstein_loss_generator(fake_output)
    
        gradients_of_generator = tape.gradient(
            gen_loss, gan_instance.trainable_variables
        )
        self.generator_optimizer.apply_gradients(
            zip(gradients_of_generator, gan_instance.trainable_variables)
        )
    
    @tf.function
    def train_critic(self, gan_instance:tf.keras.Model, critic:tf.keras.Model, noise: tf.Tensor, images: tf.Tensor):
        """Update the generator parameter with its optimizer
    
        :param noise: Input of the generator
        :param images: Real images as input for the discriminator.
        """
    
        with tf.GradientTape() as tape:
            generated_images = gan_instance(noise, training=False)
            #generated_images = tf.expand_dims(generated_images, -1)
            real_output = critic(images, training=True)
            fake_output = critic(generated_images, training=True)
            disc_loss = self.wasserstein_loss_critic(real_output, fake_output)
            penalty_loss = self.gradient_penalty(critic, generated_images, images)
            disc_loss += penalty_loss * self.gradient_penalty_weight
    
        gradients_of_critic = tape.gradient(disc_loss, critic.trainable_variables)
        self.discriminator_optimizer.apply_gradients(
            zip(gradients_of_critic, critic.trainable_variables)
        )
    
    def train(self):
        print('Run: ', self.run_id, ' has started')
        count = 0
        lowest_wass = 1e5
        lowest_acf_abs = 1e5
        lowest_acf_nonabs = 1e5
        noise_cst = tf.random.uniform([self.train_time_series.shape[0], self.noise_dim], minval=0, maxval=2*np.pi, seed = 0)
        train_dataset = tf.data.Dataset.from_tensor_slices(self.train_time_series).shuffle(self.BUFFER_SIZE).batch(self.BATCH_SIZE * self.nb_steps_update_critic)
        lowest_wass_epoch = 0
        for epoch in range(self.epochs):    
            for image_batch in train_dataset:
                batches_discriminator = tf.data.Dataset.from_tensor_slices(image_batch).batch(self.BATCH_SIZE)
                for discriminator_batch in batches_discriminator:
                    noise = tf.random.uniform([discriminator_batch.shape[0], self.noise_dim], minval=0, maxval=2*np.pi)
    
                    #discriminator_batch = tf.expand_dims(discriminator_batch, -1)
                    
                    self.train_critic(self.generator, self.discriminator, noise, discriminator_batch)
    
                noise = tf.random.uniform([self.BATCH_SIZE, self.noise_dim],minval=0, maxval=2*np.pi)
                self.train_generator(self.generator, self.discriminator, noise)
    
            #### lOGGING / tESTING
            generated_images = self.generator(noise_cst, training=False)
            #generated_images = tf.expand_dims(generated_images, -1)
            #print(np.shape(train_time_series))
            #train_time_series = np.expand_dims(train_time_series, -1)
            #train_ts = tf.expand_dims(self.train_time_series, -1)
            real_output = self.discriminator(self.train_time_series, training=False)
            fake_output = self.discriminator(generated_images, training=False)
    
            gen_loss = self.wasserstein_loss_generator(fake_output)
            disc_loss = self.wasserstein_loss_critic(real_output, fake_output)
            self.loss_gen.append(gen_loss.numpy())
            self.loss_disc.append(disc_loss.numpy())
            if epoch%5 == 0:
              noise = tf.random.uniform([1000, self.noise_dim], minval=0, maxval=2*np.pi)
              
              generated_data = self.generator(noise, training=False).numpy()
              generated_data_transformed = dh.inverse_transform(generated_data, self.transform_params)    
              metric  = st.metrics(generated_data_transformed, self.log_returns_sp500, self.benchmark_lags, self.benchmarks, only_EMD = True)
              self.loss_wass.append(metric[0])
              self.loss_epochs.append(epoch)
              print('Run_id {}, found EMD {} at epoch {}'.format(self.run_id, metric[0], epoch))
              if metric[0] <= lowest_wass:  
                count +=1
                lowest_wass = metric[0]
                lowest_wass_epoch = epoch
                self.generator.save_weights(self.weight_path+"/lowest_wass")
              if epoch%100 == 0:
                  st.QQ_plot(generated_data_transformed, self.log_returns_sp500, 'QQ plot at epoch {}'.format(str(epoch)), xlabel = 'Quantiles generated', ylabel = 'Quantiles SP 500', limit = [-0.04,0.04], show = False, path = self.plot_path+'/QQ_plot_epoch_{}.pdf'.format(str(epoch)))
                  self.generator.save_weights(self.weight_path+"/weights_epoch_{}".format(str(epoch)))
        
                  
        
            
                
        np.savetxt(self.metrics_path+'/loss_gen.txt', np.array(self.loss_gen))
        np.savetxt(self.metrics_path+'/loss_disc.txt', np.array(self.loss_disc))
        np.savetxt(self.metrics_path+'/loss_wass.txt', np.array(self.loss_wass))
        np.savetxt(self.metrics_path+'/loss_epochs.txt', np.array(self.loss_epochs))
        np.savetxt(self.metrics_path+'/best_metrics.txt', np.array([lowest_wass, lowest_wass_epoch]))
        
        
    def generate_samples(self, weights_path):
        self.generator.load_weights(weights_path)
        noise = tf.random.uniform([1000, self.noise_dim], minval=0, maxval=2*np.pi)              
        generated_data = self.generator(noise, training=False).numpy()
        generated_data_transformed = dh.inverse_transform(generated_data, self.transform_params)    
        st.QQ_plot(generated_data_transformed, self.log_returns_sp500, 'QQ plot at epoch best epoch', xlabel = 'Quantiles generated', ylabel = 'Quantiles SP 500', limit = [-0.04,0.04], show = True, path = './QQ_best.pdf')
        metric  = st.metrics(generated_data_transformed, self.log_returns_sp500, self.benchmark_lags, self.benchmarks, only_EMD = True)
        print(metric[0])
        return generated_data_transformed
    
def sweep_layers(N_low, N_high, N_concurrent_runs):
    #ray.init()
    timestamp = dt.now().strftime("%Y%m%d_%H%M%S")
    path_master = './sweep_layers_'+timestamp
    os.mkdir(path_master)
    layers_range = np.arange(N_low, N_high+1)
    for n_layer in layers_range:
        print('------------------------------------')
        print('Runs started for n_layer = ', n_layer)
        print('------------------------------------')
        path_layer = path_master+'/{}_layers'.format(n_layer)
        os.mkdir(path_layer)
        GANS = [quantum_GAN.remote(2, 5, 4, n_layer, 4000, save = True, run_id = i, path = path_layer) for i in range(N_concurrent_runs)]
        trained_GANS = [gan.train.remote() for gan in GANS]
        ray.get(trained_GANS)


def process_results_layers(path_master):
    print(path_master)
    layer_folders = os.listdir(path_master)
    #layer_folders.remove('code_copy')
    layer_folders.sort()
    layer_paths = []
    for folder in layer_folders:
        layer_paths.append(path_master+'/'+folder)    
    print(layer_paths)
    runs = os.listdir(layer_paths[0])
    runs.sort()
    print(runs)
    
    layer_EMDs = np.zeros((len(layer_paths),len(runs)))
    loss_wass = np.zeros((len(layer_paths),len(runs), 800))
    for i, layer_path in enumerate(layer_paths):        
        for j,run in enumerate(runs):
            run_path = layer_path+'/'+run
            metric_path = run_path+'/metrics'
            best_metrics = np.loadtxt(metric_path+'/best_metrics.txt')
            lw = np.loadtxt(metric_path+'/loss_wass.txt')
            print(best_metrics)
            layer_EMDs[i][j] = best_metrics[0]
            loss_wass[i][j] = lw
    #lowest_EMD_average.append(np.mean(layer_EMDs))
    #lowest_EMD_std.append(np.std(layer_EMDs, ddof = 1))
    print(layer_EMDs)
    lowest_EMD_average = np.average(layer_EMDs, axis = 1)
    lowest_EMD_err = np.std(layer_EMDs, axis = 1, ddof = 1)/np.sqrt(layer_EMDs.shape[1])
    loss_wass_average = np.average(loss_wass, axis = 1)
    loss_wass_err = np.std(loss_wass, axis = 1, ddof = 1)/np.sqrt(loss_wass.shape[1])
    a = quantum_GAN(2, 5, 4, 4, 4000, save = False)
    print('oi', loss_wass_average.shape)
    gen_samp = a.generate_samples( './sweep_layers_20211215_122954/4_layers/run_0/weights/lowest_wass')
    gen_samp = a.generate_samples( './sweep_layers_20211215_122954/4_layers/run_1/weights/lowest_wass')
    gen_samp = a.generate_samples( './sweep_layers_20211215_122954/4_layers/run_2/weights/lowest_wass')
    gen_samp = a.generate_samples( './sweep_layers_20211215_122954/4_layers/run_3/weights/lowest_wass')
    plt.plot(range(1,len(layer_paths)+1), lowest_EMD_average, label = 'Mean lowest EMD')
    plt.fill_between(range(1,len(layer_paths)+1), lowest_EMD_average-2*lowest_EMD_err,lowest_EMD_average+2*lowest_EMD_err, alpha = 0.3, label = r'2$\sigma$ CI')
    plt.legend()
    plt.xlabel('Number of layers')
    plt.ylabel('Lowest EMD score')
    #plt.ylim(0.0004,0.0010)
    plt.show()    
    
    for i in range(0, loss_wass_average.shape[0]):
        plt.plot(range(0, loss_wass_average.shape[1]*5,5),loss_wass_average[i], label = str(i+1))
        plt.fill_between(range(0, loss_wass_average.shape[1]*5,5),loss_wass_average[i]-2*loss_wass_err[i],loss_wass_average[i]+2*loss_wass_err[i], alpha = 0.3)
    plt.legend(title = '# of layers')
    plt.xlabel('Epoch')
    plt.ylabel('EMD score')
    plt.ylim(0,0.015)
    plt.show()
    
    
    
    


In [3]:
#a = quantum_GAN(2, 5, 4, 4, 4000)
#sweep_layers(5, 5, 8)


In [4]:
#process_results_layers('./sweep_layers_20211215_122954')

In [ ]:
sweep_layers(1, 6, 15)

------------------------------------
Runs started for n_layer =  1
------------------------------------


(pid=219424) 2021-12-20 14:49:13.903017: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
(pid=219424) 2021-12-20 14:49:13.903059: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
(pid=219431) 2021-12-20 14:49:13.903020: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
(pid=219431) 2021-12-20 14:49:13.903060: I tensorflow/stream_executor/cuda/cudart_stub.cc:29] Ignore above cudart dlerror if you do not have a GPU set up on your machine.
(pid=219453) 2021-12-20 14:49:13.903017: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcud

(quantum_GAN pid=219427) WARNING:tensorflow:From /home/schwander/.conda/envs/tfq_env3/lib/python3.9/site-packages/tensorflow/python/ops/array_ops.py:5043: calling gather (from tensorflow.python.ops.array_ops) with validate_indices is deprecated and will be removed in a future version.
(quantum_GAN pid=219427) Instructions for updating:
(quantum_GAN pid=219427) The `validate_indices` argument has no effect. Indices are always validated on CPU and never validated on GPU.
(quantum_GAN pid=219447) WARNING:tensorflow:From /home/schwander/.conda/envs/tfq_env3/lib/python3.9/site-packages/tensorflow/python/ops/array_ops.py:5043: calling gather (from tensorflow.python.ops.array_ops) with validate_indices is deprecated and will be removed in a future version.
(quantum_GAN pid=219447) Instructions for updating:
(quantum_GAN pid=219447) The `validate_indices` argument has no effect. Indices are always validated on CPU and never validated on GPU.
(quantum_GAN pid=219424) WARNING:tensorflow:From /ho

(quantum_GAN pid=219447) Run:  14  has started
(quantum_GAN pid=219449) Run:  7  has started
(quantum_GAN pid=219419) Run:  4  has started
(quantum_GAN pid=219438) Run:  10  has started
(quantum_GAN pid=219427) Run:  12  has started
(quantum_GAN pid=219453) Run:  6  has started


(quantum_GAN pid=219438) WARNING:tensorflow:AutoGraph could not transform <bound method quantum_GAN.train_critic of <tensorflow.python.eager.function.TfMethodTarget object at 0x7ef87c272f70>> and will run it as-is.
(quantum_GAN pid=219438) Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
(quantum_GAN pid=219438) Cause: Unknown node type <gast.gast.Import object at 0x7ef87c317910>
(quantum_GAN pid=219438) To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert
(quantum_GAN pid=219449) WARNING:tensorflow:AutoGraph could not transform <bound method quantum_GAN.train_critic of <tensorflow.python.eager.function.TfMethodTarget object at 0x7f0a2225fac0>> and will run it as-is.
(quantum_GAN pid=219449) Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the 

...

(quantum_GAN pid=219454) 2021-12-21 02:48:30.364922: W tensorflow/core/kernels/data/model_dataset_op.cc:205] Optimization loop failed: Cancelled: Operation was cancelled
(quantum_GAN pid=219466) 2021-12-21 02:48:30.836913: W tensorflow/core/kernels/data/model_dataset_op.cc:205] Optimization loop failed: Cancelled: Operation was cancelled


(quantum_GAN pid=219454) Run_id 0, found EMD 0.0006218960028409697 at epoch 3955
(quantum_GAN pid=219460) Run_id 13, found EMD 0.0007388726719363076 at epoch 3995


(quantum_GAN pid=219452) 2021-12-21 02:48:39.057255: W tensorflow/core/kernels/data/model_dataset_op.cc:205] Optimization loop failed: Cancelled: Operation was cancelled


(quantum_GAN pid=219455) Run_id 14, found EMD 0.006577405788527214 at epoch 3970


(quantum_GAN pid=219458) 2021-12-21 02:48:40.813399: W tensorflow/core/kernels/data/model_dataset_op.cc:205] Optimization loop failed: Cancelled: Operation was cancelled


In [ ]:
\